# Loading and displaying incons form the prepared csv files in a map.

In [1]:
import pathlib
import glob
import pandas as pd

import folium
from folium import Map, LayerControl
from folium.plugins import MarkerCluster

from folium.raster_layers import TileLayer
from folium.plugins import FloatImage
from folium import plugins
from folium.features import CustomIcon
from folium import IFrame
import branca

import base64


C:\Users\Ramin\AppData\Local\Temp\ipykernel_15048\335876296.py:3: DeprecationWarning: 
Pyarrow will become a required dependency of pandas in the next major release of pandas (pandas 3.0),
(to allow more performant data types, such as the Arrow string type, and better interoperability with other libraries)
but was not found to be installed on your system.
If this would cause problems for you,
please provide us feedback at https://github.com/pandas-dev/pandas/issues/54466
        
  import pandas as pd


In [2]:
path = 'data/MyData'
# get all filenames under the data directory
l = [pd.read_csv(filename) for filename in glob.glob(path + "/*.csv")]

# check the list size to understand how many files will be read
print(len(l))

#  create the dataset using all files under the data directory
df = pd.concat(l, axis=0)
df.dropna()
df.reset_index(drop=True)

5


country                                      name         build_year  \
0   افغانستان                                 مسجد کبود           ۸۸۵ هجری   
1   افغانستان              آرامگاه خواجه عبدالله انصاری        ۱۴۲۵ میلادی   
2   افغانستان                                 خرقه شریف        ۱۷۶۸ میلادی   
3    ارمنستان                           صومعه هاغارتسین        ۱۲۸۱ میلادی   
4    ارمنستان                     کلیسای جامع اچمیادزین         ۳۰۳ میلادی   
5    ارمنستان                                 سواناوانک         ۸۷۴ میلادی   
6    ارمنستان                           صومعه خور ویراپ         ۶۴۲ میلادی   
7       ایران                        کلیسای تادئوس مقدس                  ?   
8       ایران               گورستان و زیارتگاه خالد نبی                  ?   
9       ایران                             حرمِ امام رضا               ۱۲۳۰   
10      ایران                   حرم شاه‌ عبدالعظیم حسنی                  ?   
11      ایران                               مسجد جمکران                  ?   
12      ایران                     آرامگاه استر و مردخای                  ?   
13      ایران                     مقبره سلطان امیر احمد                  ?   
14      ایران                          حرم فاطمه معصومه      ۹۵۰ هجری قمری   
15      ایران                               حرم شاهچراغ  سده ششم هجری قمری   
16      ایران                 آرامگاه شاه نعمت‌الله‌ولی           ۸۴۰ قمری   
17    پاکستان                  مزار حضرت امام بری سرکار                  ?   
18    پاکستان                             مزار شاه حسین                  ?   
19    پاکستان                              مسجد پادشاهی                  ?   
20    پاکستان                                داتا دربار                  ?   
21    پاکستان                              حرم میان میر                  ?   
22    پاکستان                       مقبره بابا بوله شاه                  ?   
23    پاکستان            زیارتگاه شیخ داود بندگی کرمانی                  ?   
24    پاکستان                       زیارتگاه سلطان باهو                  ?   
25    پاکستان                        مقبره شاه رکن عالم                  ?   
26    پاکستان            مقبره شمس الدین سبزواری ملتانی        ۱۳۳۰ میلادی   
27    پاکستان                  زیارتگاه بهاءالدین زکریا        ۱۲۶۲میلادی    
28    پاکستان                  آرامگاه سید خیرالدین شاه        ۱۶۱۷میلادی    
29    پاکستان  آرامگاه حضرت سید صدر الدین شاہ رضوی نقوی                  ?   
30    پاکستان                        زیارتگاه خواجه خضر                  ?   
31    پاکستان                درگاه حضرت حاجنا شاه حضوری                  ?   
32    پاکستان                آرامگاه فقير قادر بخش بيدل                  ?   
33    پاکستان                       آرامگاه ساچال سرمست                  ?   
34    پاکستان                  زیارتگاه لعل شهباز قلندر                  ?   
35    پاکستان             زیارتگاه شاه عبداللطیف بهیتای         ۱۷۷۲میلادی   
36    پاکستان                    زیارتگاه صوفی پیر منگو                  ?   
37    پاکستان                       درگاہ جمن شاہ بخاری                  ?   
38    پاکستان                      حرم عبدالله شاه قاضی                  ?   
39  ترکمنستان                      زیارتگاه پاراو بی بی                  ?   
40  ترکمنستان                                  آک ایشان                  ?   
41  ترکمنستان                               آستانه بابا                  ?   
42  ترکمنستان                               اسماموت عطا                  ?   
43  ترکمنستان                                 گوزلی آتا                  ?   
44  ترکمنستان                        مقبره  یوسف همدانی                  ?   
45  ترکمنستان                               کهنه گرگانج                  ?   
46  ترکمنستان                                  ملک بابا                  ?   

   religion                           denomination   latitude  longitude  \
0     اسلام                                    سنی  36.708333  67.111111   
1     اسلام                                   صوفی  34.374756  62.240506   
2     اسلام                      

Popup table function

In [3]:
def popup_html_table(row):
  """
  Function that extracts the information from each row of the dataframe and
  creates an html table with that information inside. This is the first part of the html for the pop up box.
  """
  #print(row)

  country = str(row['country'])
  name = row['name']
  build_year = row['build_year']
  religion = row['religion']
  remakrs = row['remakrs']
  sources = row['sources']

  img_name = df['img_name']

  #left_col_color = "#3e95b5"
  left_col_color = '#6E6C70'
  right_col_color = "#D4DCFF"


  html = """
        <!DOCTYPE html>
        <html dir = 'rtl' lang = 'fa'>
        <html>


        <center><h2 style="margin-bottom:5"; width="500px">{}</h2>""".format(name) + """</center>
        <center> <table style="height: 126px; width: 500px;">

        <tbody>
        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> کشور </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+ country + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> سال ساخت </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+build_year + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> دین </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+religion + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> توضیحات </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+remakrs + """</td>
        </tr>

        <tr>
        <td style="background-color: """+ left_col_color +""";"><span style="color: #ffffff;"> منابع </span></td>
        <td style="width: 400px;background-color: """+ right_col_color +""";">"""+sources + """</td>
        </tr>
        </tr>

        </tbody>
        </table></center>



        </html>
"""
  return html

In [4]:
# popup_frame and image

def mapper(df):

  # tiles = 'https://server.arcgisonline.com/ArcGIS/rest/services/NatGeo_World_Map/MapServer/tile/{z}/{y}/{x}'
  # attr = 'Tiles &copy; Esri &mdash; National Geographic, Esri, DeLorme, NAVTEQ, UNEP-WCMC, USGS, NASA, ESA, METI, NRCAN, GEBCO, NOAA, iPC'
  # map = folium.Map(location=(40, 55), zoom_start=3, tiles=tiles, attr = attr, control_scale=True, scrollWheelZoom=True, dragging=True)


  map = folium.Map(location=(40, 55), zoom_start=4, control_scale=True, scrollWheelZoom=True, dragging=True)

  #map = folium.Map(location=(40, 55), tiles = 'Stamen Toner', zoom_start=5, control_scale=True, scrollWheelZoom=True, dragging=True)


  icon_dict = {"اسلام":"star-and-crescent", "مسیحیت":"cross", "یهودیت":"star-of-david"}

  # Adding Marker CLusters for layer control
  mCluster = {}
  for e in df.country.unique():
    mCluster[e] = MarkerCluster(name = e)#.add_to(map)

  # main loop
  for i, row in df.iterrows():
    Filename = path+'/img/'+row['img_name']
    encoded = base64.b64encode(open(Filename, 'rb').read())
    svg = """
    <center><object data="data:image/jpg;base64,{}" width="{}" height="{} type="image/svg+xml">
    </object></center>""".format

    # Getting the first html part with the table and title
    my_html = popup_html_table(row)

    width, height, fat_wh = 500, 300, 1.1

    # Adding the encoded image
    html = my_html + svg(encoded.decode('UTF-8'), width, height)

    # constructing the frame
    iframe = branca.element.IFrame(html , width=width*fat_wh, height=height*fat_wh)
    popup  = folium.Popup(iframe, parse_html = True, max_width=600)

    # making the marker
    marker = folium.Marker(location=[row['latitude'], row['longitude']],popup=popup,
                  icon=folium.Icon(icon=icon_dict[row['religion']], prefix='fa', color = 'red'))

    mCluster[row['country']].add_child(marker).add_to(map)

  folium.LayerControl().add_to(map)

  return map

map = mapper(df)

In [5]:
map
map.save(outfile= "data/Created_Maps/map2.html")

In [7]:
map